# Compute expected lifespan from the regression outputs

### Import regression outputs for the 5 specifications 

In [2]:
import pandas as pd
import numpy as np
from itertools import product

df = pd.read_csv('../raw_data/output_clean.csv', sep=',')

df2=df.transpose()
df2.columns = df2.iloc[0]
df2.drop(df2.index[0], inplace=True)
df=df2
df.index=df.index.str.replace('_t:','')
df.index=df.index.str.replace('/:','')
columns_to_convert = ['b1', 'b2', 'b3','b4','b5']  # Specify the columns you want to convert
for column in columns_to_convert:
    df[column] = df[column].astype(float)
    
df

_t:model         b1       se1        b2       se2        b3       se3  \
_cons      0.007038   0.00009  0.005019  0.000069  0.006266  0.000093   
gamma      0.112615  0.000633  0.115123  0.000635  0.115861  0.000635   
60.AC      1.092892  0.010518  1.143737  0.011012  1.107455  0.010746   
61.AC      1.029023  0.012755  1.055005  0.013064  1.034941  0.012861   
62.AC      1.040198  0.014968  1.077806  0.015511  1.057740   0.01526   
63.AC      1.010678   0.01587  1.050681  0.016498  1.036986   0.01632   
64.AC      1.050227  0.016728  1.090197  0.017366  1.079189  0.017219   
65b.AC     1.000000         .  1.000000         .  1.000000         .   
1926.coh   1.213443  0.015645  1.162789  0.014994  1.153263  0.014881   
1930.coh   1.114559  0.013335  1.084246  0.012975  1.083997  0.012974   
1935.coh   1.022114  0.012302  1.011521  0.012176  1.015209  0.012221   
1940b.coh  1.000000         .  1.000000         .  1.000000         .   
1945.coh   0.964954  0.014408  0.977190  0.014592  0.974600  0.014554   
1950.coh   0.930901  0.021716  0.948778  0.022138  0.943132  0.022008   
0b.dis_d   1.000000         .  1.000000         .  1.000000         .   
1.dis_d    1.962717  0.023664  1.886636  0.022725  1.845746  0.022293   
0b.SEX          NaN       NaN  1.000000         .  1.000000         .   
1.SEX           NaN       NaN  1.673778  0.012339  1.767659  0.013355   
0b.imm_d        NaN       NaN       NaN       NaN  1.000000         .   
1.imm_d         NaN       NaN       NaN       NaN  0.753019  0.010193   
0b.mrt          NaN       NaN       NaN       NaN  1.000000         .   
1.mrt           NaN       NaN       NaN       NaN  0.747744  0.006126   
2.mrt           NaN       NaN       NaN       NaN  0.941607  0.026134   
1.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
2.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
3b.p_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
4.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
5.p_lvl         NaN       NaN       NaN       NaN       NaN       NaN   
0.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
1.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
2.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
3b.pp_lvl       NaN       NaN       NaN       NaN       NaN       NaN   
4.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   
5.pp_lvl        NaN       NaN       NaN       NaN       NaN       NaN   

_t:model         b4       se4        b5       se5         N   N_fail  
_cons      0.005678  0.000095  0.005088  0.000095  330645.0  81665.0  
gamma      0.116237  0.000635  0.118094  0.000637       NaN      NaN  
60.AC      1.115344  0.010845  1.125327  0.010943       NaN      NaN  
61.AC      1.040113  0.012949  1.042773  0.012958       NaN      NaN  
62.AC      1.063278  0.015352  1.066493  0.015401       NaN      NaN  
63.AC      1.042528  0.016413  1.036530  0.016312       NaN      NaN  
64.AC      1.089358  0.017385  1.048721  0.016744       NaN      NaN  
65b.AC     1.000000         .  1.000000         .       NaN      NaN  
1926.coh   1.142571  0.014757  1.173189  0.015157       NaN      NaN  
1930.coh   1.080264  0.012934  1.094715  0.013115       NaN      NaN  
1935.coh   1.016474  0.012235  1.017693   0.01225       NaN      NaN  
1940b.coh  1.000000         .  1.000000         .       NaN      NaN  
1945.coh   0.974644  0.014554  0.967176  0.014445       NaN      NaN  
1950.coh   0.941511   0.02197  0.877236  0.020504       NaN      NaN  
0b.dis_d   1.000000         .  1.000000         .       NaN      NaN  
1.dis_d    1.859657  0.022597  1.778348  0.021629       NaN      NaN  
0b.SEX     1.000000         .  1.000000         .       NaN      NaN  
1.SEX      1.957169  0.015962  1.876737  0.015424       NaN      NaN  
0b.imm_d   1.000000         .  1.000000         .       NaN      NaN  
1.imm_d    0.727781  0.0

## Compute the hazard rate for $t \in [-5,45]$

$ h(t)=\beta_{0}\prod(\beta_{j})\exp{(\gamma*t)} $, where

$\beta_{0}$ is the constant

$\beta_{j}$ is the hazard ratio of binary variable j

$\gamma$ is the gompertz parameter

$t$ is the time relative to 65 (so we compute for ages 60 to 110)

In [3]:
def get_hazard(in_df, out_df):
    #consider the 5 models imported separately
    for model in range(1, 6):
        model_name = f'b{model}'
        #extract the gamma and constant
        gamma = float(in_df.at['gamma', model_name])
        cons = float(in_df.at['_cons', model_name])
        
        #for each of our variable, 
        #extract the first characters of the index to know what level we are considering
        #extract the hazard ratio
        ac_values = [(index[:2], value) for index, value in in_df.loc[in_df.index.str.endswith('.AC'), model_name].items()]
        coh_values = [(index[:4], value) for index, value in in_df.loc[in_df.index.str.endswith('.coh'), model_name].items()]
        dis_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.dis_d'), model_name].items()]
        sex_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.SEX'), model_name].items()] if model_name in ['b2', 'b3', 'b4', 'b5'] else [(99, 1)]
        imm_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.imm_d'), model_name].items()] if model_name in ['b3', 'b4', 'b5'] else [(99, 1)]
        mrt_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.mrt'), model_name].items()] if model_name in ['b3', 'b4', 'b5'] else [(99, 1)]
        pen_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.p_lvl'), model_name].items()] if model_name in ['b4', 'b5'] else [(99, 1)]
        ppen_values = [(index[:1], value) for index, value in in_df.loc[in_df.index.str.endswith('.pp_lvl'), model_name].items()] if model_name == 'b5' else [(99, 1)]
        
        #define the age range we want to generate the hazard rate on
        t = np.arange(-5,46)
        #generate all possible combinations of values
        combinations = product(ac_values, coh_values, dis_values, sex_values, imm_values, mrt_values, pen_values, ppen_values)
        for ac, coh, dis, sex, imm, mrt, pen, ppen in combinations:
            #compute hazard rate
            fct = cons * ac[1] * coh[1] * dis[1] * sex[1] * imm[1] * mrt[1] * pen[1] * ppen[1] * np.exp(t * gamma)
            #store the characteristics used in computing and the hazard rate
            new_row = {'AC': ac[0], 'coh': coh[0], 'dis': dis[0], 'sex': sex[0], 'imm': imm[0], 'mrt': mrt[0], 'p': pen[0], 'pp': ppen[0], 't': t, 'ht': fct}
            #append stored estimates to the out dataframe
            out_df = out_df.append(new_row, ignore_index=True)
    return out_df

#initialize empty dataframe to receive out_df
hazard = pd.DataFrame(columns=['AC', 'coh', 'dis', 'sex', 'imm', 'mrt', 'p', 'pp', 't', 'ht'])
#run the function
hazard = get_hazard(df, hazard)


C:\Users\Xavier\AppData\Local\Temp\ipykernel_3700\1699355871.py:31: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_3700\1699355871.py:31: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_3700\1699355871.py:31: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ignore_index=True)
C:\Users\Xavier\AppData\Local\Temp\ipykernel_3700\1699355871.py:31: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  out_df = out_df.append(new_row, ign

## Change the previous table which had the hazard rate saved as a list to a dataframe that has the hazard rate saved as a column with all characteristics used in computing

In [4]:
#initialize receiving df
table=pd.DataFrame()
#multiply all characteristics by 51 so that they are lists like the hazard rate
for var in ['AC','coh','dis','sex','imm','mrt','p','pp']:
    hazard[var] = hazard[var].apply(lambda x: [x] * 51)
    table[var]=hazard[var].explode()
#explode all series into a long form dataframe    
table['t'] = hazard['t'].explode()
table['ht'] = hazard['ht'].explode()
table=table.reset_index()
#column identity serves to indicate separate combinations of characteristics used in computing hazard rate
table=table.rename(columns={'index':'identity'})
table.head(60)

identity  AC   coh dis sex imm mrt   p  pp   t        ht
0          0  60  1926   0  99  99  99  99  99  -5  0.005315
1          0  60  1926   0  99  99  99  99  99  -4  0.005949
2          0  60  1926   0  99  99  99  99  99  -3  0.006658
3          0  60  1926   0  99  99  99  99  99  -2  0.007452
4          0  60  1926   0  99  99  99  99  99  -1   0.00834
5          0  60  1926   0  99  99  99  99  99   0  0.009334
6          0  60  1926   0  99  99  99  99  99   1  0.010447
7          0  60  1926   0  99  99  99  99  99   2  0.011692
8          0  60  1926   0  99  99  99  99  99   3  0.013086
9          0  60  1926   0  99  99  99  99  99   4  0.014645
10         0  60  1926   0  99  99  99  99  99   5  0.016391
11         0  60  1926   0  99  99  99  99  99   6  0.018345
12         0  60  1926   0  99  99  99  99  99   7  0.020532
13         0  60  1926   0  99  99  99  99  99   8  0.022979
14         0  60  1926   0  99  99  99  99  99   9  0.025718
15         0  60  1926   0  99  99  99  99  99  10  0.028784
16         0  60  1926   0  99  99  99  99  99  11  0.032215
17         0  60  1926   0  99  99  99  99  99  12  0.036055
18         0  60  1926   0  99  99  99  99  99  13  0.040353
19         0  60  1926   0  99  99  99  99  99  14  0.045163
20         0  60  1926   0  99  99  99  99  99  15  0.050547
21         0  60  1926   0  99  99  99  99  99  16  0.056572
22         0  60  1926   0  99  99  99  99  99  17  0.063316
23         0  60  1926   0  99  99  99  99  99  18  0.070863
24         0  60  1926   0  99  99  99  99  99  19   0.07931
25         0  60  1926   0  99  99  99  99  99  20  0.088764
26         0  60  1926   0  99  99  99  99  99  21  0.099344
27         0  60  1926   0  99  99  99  99  99  22  0.111186
28         0  60  1926   0  99  99  99  99  99  23   0.12444
29         0  60  1926   0  99  99  99  99  99  24  0.139274
30         0  60  1926   0  99  99  99  99  99  25  0.155875
31         0  60  1926   0  99  99  99  99  99  26  0.174456
32         0  60  1926   0  99  99  99  99  99  27  0.195251
33         0  60  1926   0  99  99  99  99  99  28  0.218525
34         0  60  1926   0  99  99  99  99  99  29  0.244574
35         0  60  1926   0  99  99  99  99  99  30  0.273727
36         0  60  1926   0  99  99  99  99  99  31  0.306356
37         0  60  1926   0  99  99  99  99  99  32  0.342874
38         0  60  1926   0  99  99  99  99  99  33  0.383745
39         0  60  1926   0  99  99  99  99  99  34  0.429488
40         0  60  1926   0  99  99  99  99  99  35  0.480683
41         0  60  1926   0  99  99  99  99  99  36  0.537982
42         0  60  1926   0  99  99  99  99  99  37   0.60211
43         0  60  1926   0  99  99  99  99  99  38  0.673882
44         0  60  1926   0  99  99  99  99  99  39   0.75421
45         0  60  1926   0  99  99  99  99  99  40  0.844113
46         0  60  1926   0  99  99  99  99  99  41  0.944732
47         0  60  1926   0  99  99  99  99  99  42  1.057346
48         0  60  1926   0  99  99  99  99  99  43  1.183383
49         0  60  1926   0  99  99  99  99  99  44  1.324443
50         0  60  1926   0  99  99  99  99  99  45  1.482319
51         1  60  1926   1  99  99  99  99  99  -5  0.010432
52         1  60  1926   1  99  99  99  99  99  -4  0.011676
53         1  60  1926   1  99  99  99  99  99  -3  0.013068
54         1  60  1926   1  99  99  99  99  99  -2  0.014626
55         1  60  1926   1  99  99  99  99  99  -1  0.016369
56         1  60  1926   1  99  99  99  99  99   0   0.01832
57         1  60  1926   1  99  99  99  99  99   1  0.020504
58         1  60  1926   1  99  99  99  99  99   2  0.022948
59         1  60  1926   1  99  99  99  99  99   3  0.025683

## Compute lx and dx

$lx_{-5}=N_{-5}$

$lx_{t}=lx_{t-1}-dx_{t}, \forall t>-5$

$dx_{t}=lx_{t}*h(t)$

In [5]:
# Get initial lx value (t=0)
initial_lx = df['N'].values[0]

# Initialize lx and dx lists to store calculated values
lx_values = []
dx_values = []

# Iterate through each row in the DataFrame
for index, row in table.iterrows():
    t = row['t']
    if t == -5:
        lx=initial_lx
    else:
        # Calculate lx for t>60
        lx = lx_values[-1] - dx_values[-1]
    ht = row['ht']
    dx = lx * ht
    #append calculated values to the lists
    dx_values.append(dx)
    lx_values.append(lx)


# Update 'lx' and 'dx' columns in the DataFrame
table['lx'] = lx_values
table['dx'] = dx_values

## Compute Lx

$Lx_{-5}=\frac{lx_{-5}+lx_{-4}}{2}$

$Lx_{t}=Lx_{t-1}-dx_{t}$


In [6]:
Lx_values = []

# Iterate through each row in the DataFrame
for index, row in table.iterrows():
    t = row['t']
    lx = row['lx']
    dx = row['dx']
    if t == -5:
        #for the first year, Lx is the average of Lx at t=0 and t=1
        Lx =(lx + table.iloc[index+1]['lx'])/2
    else:
        # Calculate Lx for other t
        Lx = Lx_values[-1] - dx
    Lx_values.append(Lx)


# Update 'Lx' columns in the DataFrame
table['Lx'] = Lx_values

## Compute Tx as cumsum of Lx
$ Tx_{k}=\sum_{t=k}^{50}Lx_{k}$

In [7]:
#Tx

group=table.groupby('identity')
tx_group = group['Lx'].apply(lambda x: x[::-1].cumsum()[::-1])
table['Tx']=tx_group

C:\Users\Xavier\AppData\Local\Temp\ipykernel_3700\89395087.py:4: FutureWarning: Not prepending group keys to the result index of transform-like apply. In the future, the group keys will be included in the index, regardless of whether the applied function returns a like-indexed object.
To preserve the previous behavior, use

	>>> .groupby(..., group_keys=False)

To adopt the future behavior and silence this warning, use 

	>>> .groupby(..., group_keys=True)
  tx_group = group['Lx'].apply(lambda x: x[::-1].cumsum()[::-1])


## Compute expected lifespan
$ex=\frac{Tx}{Lx}$

In [8]:
#expected lifespan
table['ex']=table['Tx']/table['Lx']

table.head(5)

identity  AC   coh dis sex imm mrt   p  pp   t        ht             lx  \
0         0  60  1926   0  99  99  99  99  99  -5  0.005315  330645.000000   
1         0  60  1926   0  99  99  99  99  99  -4  0.005949  328887.516332   
2         0  60  1926   0  99  99  99  99  99  -3  0.006658  326930.993257   
3         0  60  1926   0  99  99  99  99  99  -2  0.007452  324754.276474   
4         0  60  1926   0  99  99  99  99  99  -1   0.00834  322334.312184   

            dx             Lx            Tx         ex  
0  1757.483668  329766.258166  7.703928e+06  23.361782  
1  1956.523075  327809.735091  7.374161e+06  22.495248  
2  2176.716783  325633.018308  7.046352e+06  21.638934  
3  2419.964290  323213.054018  6.720719e+06  20.793463  
4  2688.245105  320524.808913  6.397505e+06  19.959471

## Isolate expected lifespan at 60 and 65

In [18]:
# Check if values in 't' column are equal to -5
mask60 = table['t'] == -5
mask65 = table['t'] == 0

# Assign values from 'ex' column to 'ex60' column where 't' equals -5
table.loc[mask60, 'ex60'] = table.loc[mask60, 'ex']
table.loc[mask65, 'ex65'] = table.loc[mask65, 'ex']
table['ex65']=table.groupby('identity')['ex65'].transform('max')
table.head(10)

identity  AC   coh dis sex imm mrt   p  pp   t        ht             lx  \
0         0  60  1926   0  99  99  99  99  99  -5  0.005315  330645.000000   
1         0  60  1926   0  99  99  99  99  99  -4  0.005949  328887.516332   
2         0  60  1926   0  99  99  99  99  99  -3  0.006658  326930.993257   
3         0  60  1926   0  99  99  99  99  99  -2  0.007452  324754.276474   
4         0  60  1926   0  99  99  99  99  99  -1   0.00834  322334.312184   
5         0  60  1926   0  99  99  99  99  99   0  0.009334  319646.067079   
6         0  60  1926   0  99  99  99  99  99   1  0.010447  316662.471620   
7         0  60  1926   0  99  99  99  99  99   2  0.011692  313354.396094   
8         0  60  1926   0  99  99  99  99  99   3  0.013086  309690.671181   
9         0  60  1926   0  99  99  99  99  99   4  0.014645  305638.167332   

            dx             Lx            Tx         ex       ex60       ex65  
0  1757.483668  329766.258166  7.703928e+06  23.361782  23.361782  19.137612  
1  1956.523075  327809.735091  7.374161e+06  22.495248        NaN  19.137612  
2  2176.716783  325633.018308  7.046352e+06  21.638934        NaN  19.137612  
3  2419.964290  323213.054018  6.720719e+06  20.793463        NaN  19.137612  
4  2688.245105  320524.808913  6.397505e+06  19.959471        NaN  19.137612  
5  2983.595459  317541.213454  6.076981e+06  19.137612        NaN  19.137612  
6  3308.075526  314233.137928  5.759439e+06  18.328555        NaN  19.137612  
7  3663.724913  310569.413015  5.445206e+06  17.532977        NaN  19.137612  
8  4052.503848  306516.909167  5.134637e+06  16.751562        NaN  19.137612  
9  4476.217145  302040.692022  4.828120e+06  15.984998        NaN  19.137612

## Create final dataset, only containing characteristics used in computing expected lifespan and expected lifespan at 60 and 65

In [19]:
unique = table[table['ex60'].notna()]
df_final=pd.DataFrame()
df_final['AC']=unique['AC']
df_final['coh']=unique['coh']
df_final['dis']=unique['dis']
df_final['sex']=unique['sex']
df_final['imm']=unique['imm']
df_final['mrt']=unique['mrt']
df_final['p']=unique['p']
df_final['pp']=unique['pp']
df_final['ex60']=unique['ex60']
df_final['ex65']=unique['ex65']
df_final=df_final.reset_index()
del df_final['index']
df_final

AC   coh dis sex imm mrt   p  pp       ex60       ex65
0      60  1926   0  99  99  99  99  99  23.361782  19.137612
1      60  1926   1  99  99  99  99  99  18.435131  14.609205
2      60  1930   0  99  99  99  99  99  24.014652  19.749099
3      60  1930   1  99  99  99  99  99  19.027926  15.144502
4      60  1935   0  99  99  99  99  99  24.685810  20.379969
...    ..   ...  ..  ..  ..  ..  ..  ..        ...        ...
31315  65  1950   1   1   1   2   5   1  21.379046  17.227987
31316  65  1950   1   1   1   2   5   2  21.645223  17.474512
31317  65  1950   1   1   1   2   5   3  21.806265  17.623885
31318  65  1950   1   1   1   2   5   4  22.004739  17.808203
31319  65  1950   1   1   1   2   5   5  23.946452  19.623565

[31320 rows x 10 columns]

In [20]:
for num in '60', '65':
    filter = (df_final[
    (df_final['AC'] == num) &          # 60 61 62 63 64 65
    (df_final['coh'] == '1950') &      # 1926 1930 1935 1940 1945 1950
    (df_final['sex'] == '1') &         # 0(w) 1(m) No
    (df_final['dis'] == '0') &         # 0(no) 1(yes)
    (df_final['imm'] == '1') &         # 0(no) 1(yes) No
    (df_final['mrt'] == '1') &         # 0(div/single) 1(marr) 2(widow) No
    (df_final['p'] == '3') &           # 1 2 3 4 5 No
    (df_final['pp'] == '1')])          # 0(no) 1 2 3 4 5 No
    if num=='60':
        sum_60 = filter['ex60'].describe().loc['mean']
    elif num=='65':
        sum_65 = filter['ex60'].describe().loc['mean']
print("Expected lifespan when claiming: @ 60:", round(sum_60,2), "@65", round(sum_65,2))

Expected lifespan when claiming: @ 60: 26.45 @65 27.36


In [21]:
df_final.to_csv('../data/ex.csv')